# Tensorflow Tutorial

## Convulution Network

The TensorFlow layers module provides a high-level API that makes it easy to construct a neural network. It provides methods that facilitate the creation of dense (fully connected) layers and convolutional layers, adding activation functions, and applying dropout regularization. In this tutorial, you'll learn how to use layers to build a convolutional neural network model to recognize the handwritten digits in the MNIST data set.

In [9]:
from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

import numpy as np
import tensorflow as tf

tf.logging.set_verbosity(tf.logging.INFO)


def cnn_model_fn(features, labels, mode):
    """Model function for CNN"""
    input_layer = tf.reshape(features["x"], [-1, 28, 28 ,1])
    
    conv1 = tf.layers.conv2d( inputs = input_layer,
                            filters = 32,
                            kernel_size = [5,5],
                            padding = "same",
                            activation = tf.nn.relu)
    
    pool1 = tf.layers.max_pooling2d(inputs = conv1, pool_size = [2, 2],
                                   strides = 2)
    
    conv2 = tf.layers.conv2d(inputs = pool1,
                            filters = 64,
                            kernel_size = [5, 5],
                            padding = "same",
                            activation = tf.nn.relu)
    
    pool2 = tf.layers.max_pooling2d(inputs = conv2, pool_size =[2, 2],
                                   strides = 2)
    
    pool2_flat = tf.reshape(pool2, [-1, 7 * 7 * 64])
    dense = tf.layers.dense(inputs = pool2_flat, units = 1024, activation = tf.nn.relu)
    dropout = tf.layers.dropout( inputs = dense, rate =0.4, training=mode == tf.estimator.ModeKeys.TRAIN)
    
    logits = tf.layers.dense( inputs= dropout, units =10)
    
    predictions = {
        "classes": tf.argmax(input= logits, axis=1),
        "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
    }
    
    if mode == tf.estimator.ModeKeys.PREDICT:
        return tf.estimator.EstimatorSpec(mode = mode, predictions= predictions)
    
    loss = tf.losses.sparse_softmax_cross_entropy(labels= labels, logits=logits)
    
    if mode == tf.estimator.ModeKeys.TRAIN:
        optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001)
        train_op = optimizer.minimize(loss = loss,
            global_step = tf.train.get_global_step())
        return tf.estimator.EstimatorSpec(mode= mode, loss = loss, train_op= train_op)
    
    eval_metric_ops = {
        "accuracy": tf.metrics.accuracy(
        labels = labels, predictions = predictions["classes"])
    }
    return tf.estimator.EstimatorSpec(
    mode=mode, loss=loss, eval_metric_ops= eval_metric_ops)

In [10]:
def main():
    mnist = tf.contrib.learn.datasets.load_dataset("mnist")
    train_data = mnist.train.images
    train_labels = np.asarray(mnist.train.labels, dtype=np.int32)
    eval_data = mnist.test.images
    eval_labels = np.asarray(mnist.test.labels, dtype=np.int32)
    mnist_classifier = tf.estimator.Estimator(
    model_fn = cnn_model_fn, model_dir = "/home/prakhar/Desktop/deeplearning/")
    tensors_to_log = {"probabilities": "softmax_tensor"}
    logging_hook = tf.train.LoggingTensorHook(
        tensors= tensors_to_log, every_n_iter= 50)
    train_input_fn = tf.estimator.inputs.numpy_input_fn(
        x = {"x": train_data},
        y= train_labels,
        batch_size= 100,
        num_epochs =None,
        shuffle = True)
    mnist_classifier.train(
        input_fn = train_input_fn,
        steps = 20000,
        hooks = [logging_hook])

In [11]:
main()

Extracting MNIST-data/train-images-idx3-ubyte.gz
Extracting MNIST-data/train-labels-idx1-ubyte.gz
Extracting MNIST-data/t10k-images-idx3-ubyte.gz
Extracting MNIST-data/t10k-labels-idx1-ubyte.gz
INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_save_checkpoints_secs': 600, '_session_config': None, '_keep_checkpoint_max': 5, '_task_type': 'worker', '_is_chief': True, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x7fc3600e6e50>, '_save_checkpoints_steps': None, '_keep_checkpoint_every_n_hours': 10000, '_service': None, '_num_ps_replicas': 0, '_tf_random_seed': None, '_master': '', '_num_worker_replicas': 1, '_task_id': 0, '_log_step_count_steps': 100, '_model_dir': '/home/prakhar/Desktop/deeplearning/', '_save_summary_steps': 100}
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Saving checkpoints for 1 into /home/prakhar/Desktop/deeplearning/model.ckpt.
INFO:tensorflow:probabilities = [[ 0.09524181  0.0897573   0.10905021  

INFO:tensorflow:loss = 2.28999, step = 1
INFO:tensorflow:probabilities = [[ 0.09999511  0.07925678  0.11102185  0.09907605  0.10271827  0.08636016
   0.11451945  0.08987528  0.11040985  0.1067672 ]
 [ 0.11071275  0.08374206  0.08403178  0.0988912   0.09298275  0.10476109
   0.12967874  0.09622958  0.10782715  0.09114292]
 [ 0.09430338  0.08484252  0.09773678  0.08566283  0.10202459  0.09930475
   0.11384925  0.09674064  0.12685744  0.09867776]
 [ 0.09540319  0.10717368  0.09517816  0.10280731  0.09205346  0.09165224
   0.10979607  0.09281375  0.11101437  0.1021077 ]
 [ 0.10170566  0.09534083  0.09296147  0.09716731  0.10594295  0.09039415
   0.10878697  0.10313834  0.11088134  0.0936809 ]
 [ 0.10066493  0.09302995  0.09863226  0.10717171  0.09267893  0.09266435
   0.13445704  0.09548877  0.10068834  0.08452373]
 [ 0.10006765  0.09994783  0.08408701  0.10275609  0.10383147  0.07950898
   0.1192161   0.09504701  0.12281939  0.09271851]
 [ 0.09900796  0.09492666  0.09506753  0.11208726  0

INFO:tensorflow:global_step/sec: 50.134
INFO:tensorflow:probabilities = [[ 0.09662128  0.08788911  0.09765255  0.09309267  0.08470178  0.08514126
   0.11653593  0.11641103  0.11282641  0.10912798]
 [ 0.10793385  0.08894492  0.09351255  0.08628454  0.09581003  0.10217983
   0.11116906  0.10797753  0.11447224  0.09171548]
 [ 0.10567697  0.08147245  0.07980306  0.10648742  0.10144321  0.08277427
   0.12471556  0.10364658  0.11229958  0.10168088]
 [ 0.10328519  0.09248012  0.09370039  0.09294339  0.0962523   0.08680347
   0.12640007  0.10244421  0.11490905  0.09078178]
 [ 0.10971999  0.09710061  0.09950282  0.09803723  0.11386885  0.09236059
   0.09557064  0.0944581   0.10640699  0.09297418]
 [ 0.09216846  0.08566697  0.09583855  0.10273378  0.09631179  0.09083062
   0.10632589  0.10015816  0.12749834  0.10246745]
 [ 0.1088246   0.09399377  0.08577465  0.11353415  0.09926581  0.09373394
   0.1011332   0.10135002  0.10771558  0.0946743 ]
 [ 0.09316432  0.09403632  0.09835289  0.09903794  0.

INFO:tensorflow:loss = 2.29146, step = 101 (1.998 sec)
INFO:tensorflow:probabilities = [[ 0.08780603  0.1060731   0.0950115   0.10321144  0.09122337  0.09291161
   0.11240818  0.09164064  0.11619075  0.10352333]
 [ 0.10623326  0.09513306  0.08003295  0.1148899   0.10670264  0.09556574
   0.10171272  0.11650719  0.09556054  0.08766207]
 [ 0.10514717  0.08178773  0.09346198  0.10919556  0.10868755  0.09170841
   0.11605069  0.10049388  0.10496613  0.08850081]
 [ 0.08976801  0.09851588  0.10160477  0.11617464  0.09801868  0.0866618
   0.10924985  0.10860082  0.10419041  0.08721518]
 [ 0.08391141  0.09205516  0.0878253   0.10863322  0.09529098  0.10368796
   0.10488986  0.10542053  0.10200745  0.11627816]
 [ 0.1074994   0.09318782  0.08557456  0.11189524  0.11074463  0.08295269
   0.1104597   0.10394467  0.09752339  0.0962179 ]
 [ 0.10197047  0.08514175  0.09621165  0.09228809  0.09583984  0.09336527
   0.12836657  0.1146782   0.09322261  0.09891558]
 [ 0.09905507  0.09084032  0.08760394  

INFO:tensorflow:global_step/sec: 50.2068
INFO:tensorflow:probabilities = [[ 0.10869628  0.08262837  0.09902866  0.11627671  0.09318997  0.07675885
   0.10886638  0.09825195  0.1274478   0.08885501]
 [ 0.09778322  0.09095083  0.08605868  0.10922582  0.10610171  0.09504527
   0.11124409  0.09408473  0.11101958  0.09848604]
 [ 0.1132423   0.08876851  0.0859696   0.10559314  0.09859866  0.09225972
   0.12029167  0.10389126  0.09828924  0.09309589]
 [ 0.10573445  0.07351711  0.08926617  0.11195531  0.08406076  0.1045537
   0.11116651  0.11362553  0.11174997  0.09437057]
 [ 0.09712447  0.07854223  0.08739335  0.0873271   0.11553554  0.09470838
   0.12431249  0.10345934  0.09730928  0.11428776]
 [ 0.09143481  0.09514628  0.08003487  0.11306678  0.09587468  0.09427593
   0.10527828  0.10310877  0.10942649  0.11235312]
 [ 0.08904872  0.0836569   0.10505368  0.11327534  0.08270716  0.09504373
   0.11601565  0.10104789  0.13019326  0.08395763]
 [ 0.10792021  0.09189108  0.09183466  0.1054481   0.

...

INFO:tensorflow:global_step/sec: 48.8408
INFO:tensorflow:probabilities = [[ 0.00023895  0.00537344  0.00178476  0.03153583  0.05271656  0.08190695
   0.13908692  0.00035099  0.57651848  0.11048714]
 [ 0.00003167  0.00191598  0.02611091  0.00023184  0.96328151  0.0013179
   0.00143748  0.00524537  0.00016906  0.00025827]
 [ 0.0000002   0.          0.00000001  0.00000002  0.9998197   0.00000163
   0.00000054  0.00000421  0.00000689  0.00016673]
 [ 0.01158698  0.02207301  0.00057528  0.1554175   0.00038669  0.21458532
   0.00371131  0.00041211  0.57804179  0.01321002]
 [ 0.00044927  0.00003503  0.00407242  0.00001083  0.0002432   0.00018273
   0.99498343  0.00000104  0.0000218   0.00000013]
 [ 0.00001164  0.00013406  0.00007767  0.0000742   0.99570698  0.00003992
   0.00008522  0.00028026  0.0002197   0.00337047]
 [ 0.00002125  0.0000118   0.00004123  0.99966407  0.00000027  0.00010491
   0.00000001  0.00002305  0.00008528  0.00004815]
 [ 0.0000381   0.00000786  0.00307391  0.01935698  0.

INFO:tensorflow:loss = 0.1326, step = 19801 (2.039 sec)
INFO:tensorflow:probabilities = [[ 0.0000089   0.00000045  0.00041639  0.99929297  0.00000001  0.00018111
   0.00000055  0.00000008  0.00009485  0.00000469]
 [ 0.98877686  0.00000081  0.01071356  0.0001847   0.00006692  0.00001031
   0.00022037  0.00000203  0.00000616  0.00001827]
 [ 0.00002249  0.00024753  0.0158805   0.01010342  0.00019217  0.00007468
   0.00000639  0.96119618  0.00156699  0.01070956]
 [ 0.00000004  0.00000005  0.00001688  0.00000023  0.99990594  0.00000031
   0.00000072  0.00000047  0.00000032  0.00007502]
 [ 0.00000964  0.00000332  0.000052    0.00067323  0.00731988  0.00194411
   0.00000491  0.00392997  0.00553322  0.98052967]
 [ 0.0000069   0.00000024  0.00006154  0.99505508  0.00000545  0.00049998
   0.00000044  0.00001671  0.00015171  0.004202  ]
 [ 0.00104255  0.00000139  0.00034233  0.00136779  0.00041485  0.00268418
   0.00000059  0.61090803  0.09351769  0.28972059]
 [ 0.00000398  0.00002872  0.00017373

INFO:tensorflow:global_step/sec: 49.6852
INFO:tensorflow:probabilities = [[ 0.99862742  0.00000086  0.00055947  0.00000877  0.00002641  0.00010932
   0.00053215  0.00000737  0.00004105  0.0000873 ]
 [ 0.00012656  0.00229009  0.00710895  0.00289843  0.00027195  0.00078831
   0.00076871  0.00003366  0.98492211  0.00079129]
 [ 0.00000004  0.0000501   0.99988985  0.00005047  0.          0.
   0.00000012  0.          0.00000938  0.        ]
 [ 0.0003395   0.00012062  0.00078818  0.00012078  0.97213292  0.00053075
   0.00148486  0.00311496  0.0019388   0.01942857]
 [ 0.00106673  0.00000672  0.0004364   0.00270364  0.0032334   0.00432142
   0.00001162  0.03976377  0.00229478  0.94616157]
 [ 0.00000537  0.0000062   0.00002848  0.94717908  0.00000329  0.04934528
   0.0000296   0.00001264  0.00290748  0.00048269]
 [ 0.99446601  0.00000016  0.00012942  0.00048213  0.0000003   0.00428364
   0.00002222  0.00054483  0.00000221  0.00006904]
 [ 0.00011596  0.00000084  0.00024991  0.00000101  0.0003131

INFO:tensorflow:loss = 0.0879805, step = 19901 (2.014 sec)
INFO:tensorflow:probabilities = [[ 0.00017102  0.00000076  0.00028147  0.00000065  0.99858969  0.00003631
   0.0008076   0.0000007   0.00008165  0.00003017]
 [ 0.00009492  0.0000221   0.00073488  0.00017086  0.0089809   0.89207643
   0.09669274  0.00000603  0.00121642  0.00000473]
 [ 0.00000196  0.00000687  0.00049489  0.00000044  0.00036338  0.00004609
   0.99908531  0.00000009  0.00000082  0.0000001 ]
 [ 0.0000007   0.00000003  0.00000565  0.99854267  0.00000011  0.00007325
   0.          0.00015451  0.00000175  0.00122149]
 [ 0.00000079  0.00000228  0.00000906  0.000342    0.01037235  0.00037957
   0.00000107  0.00072906  0.00081332  0.98735052]
 [ 0.00000004  0.00000604  0.99823207  0.00174317  0.00000001  0.00000171
   0.00000194  0.00001052  0.00000456  0.        ]
 [ 0.00000029  0.          0.00000079  0.          0.00008711  0.00000026
   0.99991143  0.          0.00000017  0.        ]
 [ 0.00000043  0.00000007  0.00000

INFO:tensorflow:Saving checkpoints for 20000 into /home/prakhar/Desktop/deeplearning/model.ckpt.
INFO:tensorflow:Loss for final step: 0.0824959.
